In [1]:
%autosave 20
import numpy as np
import random

Autosaving every 20 seconds


In [2]:
class Environment():
    def __init__(self,grid_size):
        self.grid_size = np.array(grid_size)
        self.S = [np.array([i,j]) for i in range(grid_size[0]) for j in range(grid_size[1])]
        self.A = ["W","E","N","S"]
        self.A_to_coord = {"W" : [0,-1],"E" : [0,1], "N" : [-1,0], "S" : [1,0]}
        for k,v in self.A_to_coord.items():
            self.A_to_coord[k] = np.array(v)
        self.gamma = 1
        self.R = -1
        self.Terminal_states = [(0,0),(grid_size[0]-1,grid_size[1]-1)]
    def take_action(self,s,a):
        """
        Input
        s : current_state(position)
        a : action(from deterministic policy π)
        output
        s_next : state after one_step transition
        ex)
        Input : s = [0,1],a = "W"
        Output : s_next = [0,0]
        """
        r = -1
        s_next = s + self.A_to_coord[a]
        if s_next[0] < 0 or s_next[1] <0 or s_next[0] >= self.grid_size[0] or s_next[1] >= self.grid_size[1]:
            return -1,s # |S|를 넘어갈 경우, 원래 상태를 반환
        else:
            return -1,s_next
        
    def take_action_test(self):
        S = [np.array([i,j]) for i in [0,1,2,3] for j in [0,1,2,3]]
        for s in S:
            for a in self.A:
                print(s,a,self.take_action(s,a))
    def dynamics(self,s_prime,r,s,a):
        r=-1
        """
        Input
        s : current_state(position)
        a : action(from deterministic policy π)
        s_prime : all of the possible states after one-step transition
        r : immediate reward(-1)
        output
        0 if s에서 a로 움직였을때의 변화된 상태 next_s와 s_prime의 input이 다를때
        1 if s에서 a로 움직였을때의 변화된 상태 next_s와 s_prime의 input이 같을때
        즉, a방향으로 움직이면 반드시 a방향으로 감(deterministic)
        """
        s_next = self.move(s,a)
        if np.sum(s_next != s_prime)>=1:
            return 0
        else:
            return 1
    def dynamics_test(self,check_p = 1):
        r=-1
        for s in self.S:
            for a in self.A:
                for s_prime in self.S: #가능한 모든 next_state
                    if self.dynamics(s_prime,r,s,a) == check_p:
                        print(f"state : {s} action : {a} s_prime : {s_prime} dynamics : {self.dynamics(s_prime,r,s,a)}")
    def generate_π(self,uniform=False):
        """
        Input : NA
        Output : {(x,y) : {"W" : pr1,"E" : pr2 ,...}}
        ex)
        {(0,0):{"W" : 0.1, "E" : 0.2, ...},(0,1):{"W":0.4,"E":0.5...}}
        """
        π = {(i,j): {} for i in range(self.grid_size[0]) for j in range(self.grid_size[1])}
        for t in π.values():
            unnormalized_prob = np.random.rand(4)
            if uniform == False:
                prob = unnormalized_prob/np.sum(unnormalized_prob)
            else:
                prob = [0.25] * 4
            for i in range(len(self.A)):
                t[self.A[i]] = prob[i]
        return π
    def generate_V(self):
        return np.zeros((self.grid_size[0],self.grid_size[1]))

\begin{aligned}
V(S_t) \leftarrow V(S_t) +  \alpha[R_{t+1}+\gamma V(S{t+1}) - V(S_t)]
\end{aligned}

In [46]:
class TD_prediction(Environment):
    def __init__(self,grid_size = (4,4)):
        super().__init__(grid_size)
    def sampling_action(self,s,π):
        """
        Input : state,π 
        Output : action
        ex)
        Input -> (0,0),π, output -> "W" sampling from π(a|(0,0))
        """
        π_s = π[s]
        action = list(π_s.keys())
        prob = list(π_s.values())
        return np.random.choice(action,p=prob)
    def TD_prediction(self,s_0,π,α = 1,γ = 1,θ = 1,iter_nums=5000):
        self.V = self.generate_V()
        s=s_0
        Δ = 0
        for i in range(iter_nums):
            while  True:
                print("s :",s)
                a = self.sampling_action(tuple(s),π)
                print("A :",a)
                r,s_prime = self.take_action(s,a)
                print("r:",r)
                print("S':",s_prime)        
                print("======================")
                before_update = self.V[s[0]][s[1]]
                self.V[s[0]][s[1]] = self.V[s[0]][s[1]] + α*(r + γ*self.V[s_prime[0]][s_prime[1]] - self.V[s[0]][s[1]])
                Δ = max(Δ,abs(self.V[s[0]][s[1]] - before_update))
                s = s_prime
                if tuple(s) in self.Terminal_states:
                    break

td = TD_prediction()


π = td.generate_π(True)
s_0 = (1,0)


td.TD_prediction(s_0,π)
#td.take_action_test()

s : (1, 0)
A : S
r: -1
S': [2 0]
s : [2 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : E
r: -1
S': [3 1]
s : [3 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : E
r: -1
S': [3 2]
s : [3 2]
A : W
r: -1
S': [3 1]
s : [3 1]
A : W
r: -1
S': [3 0]
s : [3 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : W
r: -1
S': [3 0]
s : [3 0]
A : W
r: -1
S': [3 0]
s : [3 0]
A : W
r: -1
S': [3 0]
s : [3 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : E
r: -1
S': [3 1]
s : [3 1]
A : N
r: -1
S': [2 1]
s : [2 1]
A : W
r: -1
S': [2 0]
s : [2 0]
A : W
r: -1
S': [2 0]
s : [2 0]
A : E
r: -1
S': [2 1]
s : [2 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : W
r: -1
S': [3 0]
s : [3 0]
A : W
r: -1
S': [3 0]
s : [3 0]
A : N
r: -1
S': [2 0]
s : [2 0]
A : E
r: -1
S': [2 1]
s : [2 1]
A : N
r: -1
S': [1 1]
s : [1 1]
A : W
r: -1
S': [1 0]
s : [1 0]
A : W
r: -1
S': [1 0]
s : [1 0]
A : N
r: -1
S': [0 0]
s : [0 0]
A : N
r: -1
S': [0 0]
s : [0 0]
A : S
r: -1
S': [1 0]
s : [1 0]
A : N
r: -1
S': [0 0]
s : [0 

A : E
r: -1
S': [0 2]
s : [0 2]
A : E
r: -1
S': [0 3]
s : [0 3]
A : E
r: -1
S': [0 3]
s : [0 3]
A : S
r: -1
S': [1 3]
s : [1 3]
A : N
r: -1
S': [0 3]
s : [0 3]
A : E
r: -1
S': [0 3]
s : [0 3]
A : N
r: -1
S': [0 3]
s : [0 3]
A : N
r: -1
S': [0 3]
s : [0 3]
A : E
r: -1
S': [0 3]
s : [0 3]
A : N
r: -1
S': [0 3]
s : [0 3]
A : E
r: -1
S': [0 3]
s : [0 3]
A : N
r: -1
S': [0 3]
s : [0 3]
A : W
r: -1
S': [0 2]
s : [0 2]
A : W
r: -1
S': [0 1]
s : [0 1]
A : W
r: -1
S': [0 0]
s : [0 0]
A : W
r: -1
S': [0 0]
s : [0 0]
A : E
r: -1
S': [0 1]
s : [0 1]
A : S
r: -1
S': [1 1]
s : [1 1]
A : N
r: -1
S': [0 1]
s : [0 1]
A : S
r: -1
S': [1 1]
s : [1 1]
A : S
r: -1
S': [2 1]
s : [2 1]
A : W
r: -1
S': [2 0]
s : [2 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : W
r: -1
S': [3 0]
s : [3 0]
A : W
r: -1
S': [3 0]
s : [3 0]
A : E
r: -1
S': [3 1]
s : [3 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : N
r: -1
S': [2 1]
s : [2 1]
A : W
r: -1
S': [2 0]
s : [2 0]
A : E
r:

A : N
r: -1
S': [0 3]
s : [0 3]
A : S
r: -1
S': [1 3]
s : [1 3]
A : N
r: -1
S': [0 3]
s : [0 3]
A : E
r: -1
S': [0 3]
s : [0 3]
A : W
r: -1
S': [0 2]
s : [0 2]
A : S
r: -1
S': [1 2]
s : [1 2]
A : E
r: -1
S': [1 3]
s : [1 3]
A : N
r: -1
S': [0 3]
s : [0 3]
A : S
r: -1
S': [1 3]
s : [1 3]
A : S
r: -1
S': [2 3]
s : [2 3]
A : E
r: -1
S': [2 3]
s : [2 3]
A : N
r: -1
S': [1 3]
s : [1 3]
A : S
r: -1
S': [2 3]
s : [2 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : N
r: -1
S': [2 3]
s : [2 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : E
r: -1
S': [3 3]
s : [3 3]
A : E
r: -1
S': [3 3]
s : [3 3]
A : N
r: -1
S': [2 3]
s : [2 3]
A : N
r: -1
S': [1 3]
s : [1 3]
A : W
r: -1
S': [1 2]
s : [1 2]
A : N
r: -1
S': [0 2]
s : [0 2]
A : S
r: -1
S': [1 2]
s : [1 2]
A : N
r: -1
S': [0 2]
s : [0 2]
A : W
r: -1
S': [0 1]
s : [0 1]
A : W
r: -1
S': [0 0]
s : [0 0]
A : W
r: -1
S': [0 0]
s : [0 0]
A : E
r: -1
S': [0 1]
s : [0 1]
A : N
r: -1
S': [0 1]
s : [0 1]
A : W
r: -1
S': [0 0]
s : [0 0]
A : S
r: -1
S': [1 0]
s : [1 0]
A : W
r:

A : E
r: -1
S': [3 1]
s : [3 1]
A : N
r: -1
S': [2 1]
s : [2 1]
A : N
r: -1
S': [1 1]
s : [1 1]
A : S
r: -1
S': [2 1]
s : [2 1]
A : N
r: -1
S': [1 1]
s : [1 1]
A : W
r: -1
S': [1 0]
s : [1 0]
A : S
r: -1
S': [2 0]
s : [2 0]
A : W
r: -1
S': [2 0]
s : [2 0]
A : E
r: -1
S': [2 1]
s : [2 1]
A : W
r: -1
S': [2 0]
s : [2 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : N
r: -1
S': [2 0]
s : [2 0]
A : E
r: -1
S': [2 1]
s : [2 1]
A : W
r: -1
S': [2 0]
s : [2 0]
A : N
r: -1
S': [1 0]
s : [1 0]
A : S
r: -1
S': [2 0]
s : [2 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : N
r: -1
S': [2 0]
s : [2 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : W
r: -1
S': [3 0]
s : [3 0]
A : E
r: -1
S': [3 1]
s : [3 1]
A : E
r: -1
S': [3 2]
s : [3 2]
A : E
r: -1
S': [3 3]
s : [3 3]
A : E
r: -1
S': [3 3]
s : [3 3]
A : N
r: -1
S': [2 3]
s : [2 3]
A : W
r: -1
S': [2 2]
s : [2 2]
A : S
r: -1
S': [3 2]
s : [3 2]
A : W
r: -1
S': [3 1]
s : [3 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : W
r: -1
S': [3 0]
s : [3 0]
A : S
r:

A : W
r: -1
S': [2 0]
s : [2 0]
A : W
r: -1
S': [2 0]
s : [2 0]
A : W
r: -1
S': [2 0]
s : [2 0]
A : N
r: -1
S': [1 0]
s : [1 0]
A : N
r: -1
S': [0 0]
s : [0 0]
A : W
r: -1
S': [0 0]
s : [0 0]
A : N
r: -1
S': [0 0]
s : [0 0]
A : N
r: -1
S': [0 0]
s : [0 0]
A : W
r: -1
S': [0 0]
s : [0 0]
A : N
r: -1
S': [0 0]
s : [0 0]
A : S
r: -1
S': [1 0]
s : [1 0]
A : S
r: -1
S': [2 0]
s : [2 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : W
r: -1
S': [3 0]
s : [3 0]
A : N
r: -1
S': [2 0]
s : [2 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : W
r: -1
S': [3 0]
s : [3 0]
A : E
r: -1
S': [3 1]
s : [3 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : E
r: -1
S': [3 2]
s : [3 2]
A : S
r: -1
S': [3 2]
s : [3 2]
A : E
r: -1
S': [3 3]
s : [3 3]
A : W
r: -1
S': [3 2]
s : [3 2]
A : S
r: -1
S': [3 2]
s : [3 2]
A : W
r: -1
S': [3 1]
s : [3 1]
A : N
r: -1
S': [2 1]
s : [2 1]
A : W
r: -1
S': [2 0]
s : [2 0]
A : N
r: -1
S': [1 0]
s : [1 0]
A : W
r: -1
S': [1 0]
s : [1 0]
A : S
r: -1
S': [2 0]
s : [2 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : S
r:

...

A : S
r: -1
S': [1 1]
s : [1 1]
A : S
r: -1
S': [2 1]
s : [2 1]
A : E
r: -1
S': [2 2]
s : [2 2]
A : E
r: -1
S': [2 3]
s : [2 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : E
r: -1
S': [3 3]
s : [3 3]
A : N
r: -1
S': [2 3]
s : [2 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : N
r: -1
S': [2 3]
s : [2 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : E
r: -1
S': [3 3]
s : [3 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : E
r: -1
S': [3 3]
s : [3 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : N
r: -1
S': [2 3]
s : [2 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : E
r: -1
S': [3 3]
s : [3 3]
A : N
r: -1
S': [2 3]
s : [2 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : N
r: -1
S': [2 3]
s : [2 3]
A : W
r: -1
S': [2 2]
s : [2 2]
A : W
r: -1
S': [2 1]
s : [2 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : E
r: -1
S': [3 2]
s : [3 2]
A : E
r: -1
S': [3 3]
s : [3 3]
A : W
r: -1
S': [3 2]
s : [3 2]
A : E
r: -1
S': [3 3]
s : [3 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : W
r: -1
S': [3 2]
s : [3 2]
A : W
r: -1
S': [3 1]
s : [3 1]
A : N
r:

A : E
r: -1
S': [1 3]
s : [1 3]
A : W
r: -1
S': [1 2]
s : [1 2]
A : N
r: -1
S': [0 2]
s : [0 2]
A : N
r: -1
S': [0 2]
s : [0 2]
A : S
r: -1
S': [1 2]
s : [1 2]
A : W
r: -1
S': [1 1]
s : [1 1]
A : E
r: -1
S': [1 2]
s : [1 2]
A : N
r: -1
S': [0 2]
s : [0 2]
A : N
r: -1
S': [0 2]
s : [0 2]
A : S
r: -1
S': [1 2]
s : [1 2]
A : E
r: -1
S': [1 3]
s : [1 3]
A : N
r: -1
S': [0 3]
s : [0 3]
A : S
r: -1
S': [1 3]
s : [1 3]
A : W
r: -1
S': [1 2]
s : [1 2]
A : E
r: -1
S': [1 3]
s : [1 3]
A : W
r: -1
S': [1 2]
s : [1 2]
A : N
r: -1
S': [0 2]
s : [0 2]
A : S
r: -1
S': [1 2]
s : [1 2]
A : W
r: -1
S': [1 1]
s : [1 1]
A : S
r: -1
S': [2 1]
s : [2 1]
A : W
r: -1
S': [2 0]
s : [2 0]
A : S
r: -1
S': [3 0]
s : [3 0]
A : N
r: -1
S': [2 0]
s : [2 0]
A : N
r: -1
S': [1 0]
s : [1 0]
A : E
r: -1
S': [1 1]
s : [1 1]
A : N
r: -1
S': [0 1]
s : [0 1]
A : S
r: -1
S': [1 1]
s : [1 1]
A : S
r: -1
S': [2 1]
s : [2 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : E
r: -1
S': [3 2]
s : [3 2]
A : S
r: -1
S': [3 2]
s : [3 2]
A : N
r:

A : N
r: -1
S': [1 1]
s : [1 1]
A : S
r: -1
S': [2 1]
s : [2 1]
A : E
r: -1
S': [2 2]
s : [2 2]
A : S
r: -1
S': [3 2]
s : [3 2]
A : S
r: -1
S': [3 2]
s : [3 2]
A : E
r: -1
S': [3 3]
s : [3 3]
A : W
r: -1
S': [3 2]
s : [3 2]
A : E
r: -1
S': [3 3]
s : [3 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : E
r: -1
S': [3 3]
s : [3 3]
A : W
r: -1
S': [3 2]
s : [3 2]
A : E
r: -1
S': [3 3]
s : [3 3]
A : W
r: -1
S': [3 2]
s : [3 2]
A : E
r: -1
S': [3 3]
s : [3 3]
A : W
r: -1
S': [3 2]
s : [3 2]
A : N
r: -1
S': [2 2]
s : [2 2]
A : W
r: -1
S': [2 1]
s : [2 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : E
r: -1
S': [3 2]
s : [3 2]
A : E
r: -1
S': [3 3]
s : [3 3]
A : E
r: -1
S': [3 3]
s : [3 3]
A : N
r: -1
S': [2 3]
s : [2 3]
A : E
r: -1
S': [2 3]
s : [2 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : E
r: -1
S': [3 3]
s : [3 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : N
r: -1
S': [2 3]
s : [2 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : W
r: -1
S': [3 2]
s : [3 2]
A : E
r: -1
S': [3 3]
s : [3 3]
A : N
r:

A : E
r: -1
S': [3 3]
s : [3 3]
A : N
r: -1
S': [2 3]
s : [2 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : W
r: -1
S': [3 2]
s : [3 2]
A : N
r: -1
S': [2 2]
s : [2 2]
A : E
r: -1
S': [2 3]
s : [2 3]
A : S
r: -1
S': [3 3]
s : [3 3]
A : N
r: -1
S': [2 3]
s : [2 3]
A : E
r: -1
S': [2 3]
s : [2 3]
A : N
r: -1
S': [1 3]
s : [1 3]
A : N
r: -1
S': [0 3]
s : [0 3]
A : N
r: -1
S': [0 3]
s : [0 3]
A : W
r: -1
S': [0 2]
s : [0 2]
A : W
r: -1
S': [0 1]
s : [0 1]
A : E
r: -1
S': [0 2]
s : [0 2]
A : S
r: -1
S': [1 2]
s : [1 2]
A : W
r: -1
S': [1 1]
s : [1 1]
A : S
r: -1
S': [2 1]
s : [2 1]
A : E
r: -1
S': [2 2]
s : [2 2]
A : S
r: -1
S': [3 2]
s : [3 2]
A : N
r: -1
S': [2 2]
s : [2 2]
A : W
r: -1
S': [2 1]
s : [2 1]
A : W
r: -1
S': [2 0]
s : [2 0]
A : N
r: -1
S': [1 0]
s : [1 0]
A : N
r: -1
S': [0 0]
s : [0 0]
A : S
r: -1
S': [1 0]
s : [1 0]
A : S
r: -1
S': [2 0]
s : [2 0]
A : N
r: -1
S': [1 0]
s : [1 0]
A : W
r: -1
S': [1 0]
s : [1 0]
A : S
r: -1
S': [2 0]
s : [2 0]
A : W
r: -1
S': [2 0]
s : [2 0]
A : W
r:

A : N
r: -1
S': [2 0]
s : [2 0]
A : N
r: -1
S': [1 0]
s : [1 0]
A : W
r: -1
S': [1 0]
s : [1 0]
A : N
r: -1
S': [0 0]
s : [0 0]
A : S
r: -1
S': [1 0]
s : [1 0]
A : E
r: -1
S': [1 1]
s : [1 1]
A : N
r: -1
S': [0 1]
s : [0 1]
A : N
r: -1
S': [0 1]
s : [0 1]
A : E
r: -1
S': [0 2]
s : [0 2]
A : W
r: -1
S': [0 1]
s : [0 1]
A : W
r: -1
S': [0 0]
s : [0 0]
A : W
r: -1
S': [0 0]
s : [0 0]
A : W
r: -1
S': [0 0]
s : [0 0]
A : W
r: -1
S': [0 0]
s : [0 0]
A : E
r: -1
S': [0 1]
s : [0 1]
A : N
r: -1
S': [0 1]
s : [0 1]
A : N
r: -1
S': [0 1]
s : [0 1]
A : W
r: -1
S': [0 0]
s : [0 0]
A : E
r: -1
S': [0 1]
s : [0 1]
A : W
r: -1
S': [0 0]
s : [0 0]
A : N
r: -1
S': [0 0]
s : [0 0]
A : S
r: -1
S': [1 0]
s : [1 0]
A : E
r: -1
S': [1 1]
s : [1 1]
A : S
r: -1
S': [2 1]
s : [2 1]
A : W
r: -1
S': [2 0]
s : [2 0]
A : E
r: -1
S': [2 1]
s : [2 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : N
r: -1
S': [2 1]
s : [2 1]
A : S
r: -1
S': [3 1]
s : [3 1]
A : W
r: -1
S': [3 0]
s : [3 0]
A : E
r: -1
S': [3 1]
s : [3 1]
A : S
r:

In [47]:
td.V

array([[-1903., -1903., -2058., -2000.],
       [-1790., -1906., -1905., -1898.],
       [-1942., -1958., -2102., -1905.],
       [-2000., -1927., -1888., -1889.]])